# CS 6320 Assignment 2 - POS tagger 
## Madhumita Ramesh 
## Akshaiy Ramlinkam Jayakumar Srilatha 

<br>

<br>

## Importing datasets and analysis

In [175]:
import pandas as pd
import numpy as np

In [176]:
x_train = pd.read_csv("./data/train_x.csv")
y_train = pd.read_csv("./data/train_y.csv")

In [177]:
x_dev = pd.read_csv("./data/dev_x.csv")
y_dev = pd.read_csv("./data/dev_y.csv")
x_test = pd.read_csv("./data/test_x.csv")

In [178]:
pos = list(y_train["tag"].unique())

In [179]:
print(pos)

['O', 'NNP', ',', 'CD', 'NNS', 'JJ', 'MD', 'VB', 'DT', 'NN', 'IN', '.', 'VBZ', 'VBG', 'CC', 'VBD', 'VBN', 'RB', 'TO', 'PRP', 'RBR', 'WDT', 'VBP', 'RP', 'PRP$', 'JJS', 'POS', '``', 'EX', "''", 'WP', ':', 'JJR', 'WRB', '$', 'NNPS', 'WP$', '(', ')', 'PDT', 'RBS', 'FW', 'UH', 'SYM', 'LS', '#']


In [180]:
docs = {i:["dummy"] for i in range(1387)}
tags = {i:["dummy"] for i in range(1387)}

In [181]:
count = -1
for idx,row in x_train.iterrows():
    if(row["word"] == "-DOCSTART-"):
        count += 1
        docs[count][0] = row["word"]
    else:
        docs[count].append(row["word"])

In [182]:
count2 = -1
for idx,row in y_train.iterrows():
    if(row["tag"] == "O"):
        count2 += 1
        tags[count2][0] = row["tag"]
    else:
        tags[count2].append(row["tag"])

In [183]:
print(docs[0])
print("\n")
print(tags[0])

['-DOCSTART-', 'Pierre', 'Vinken', ',', '61', 'years', 'old', ',', 'will', 'join', 'the', 'board', 'as', 'a', 'nonexecutive', 'director', 'Nov.', '29', '.', 'Mr.', 'Vinken', 'is', 'chairman', 'of', 'Elsevier', 'N.V.', ',', 'the', 'Dutch', 'publishing', 'group', '.']


['O', 'NNP', 'NNP', ',', 'CD', 'NNS', 'JJ', ',', 'MD', 'VB', 'DT', 'NN', 'IN', 'DT', 'JJ', 'NN', 'NNP', 'CD', '.', 'NNP', 'NNP', 'VBZ', 'NN', 'IN', 'NNP', 'NNP', ',', 'DT', 'NNP', 'VBG', 'NN', '.']


In [184]:
num_tags = len(pos)

<br>

## Frequency checker to train unknown words (threshold=1)

In [185]:
freq = {}
for i in range(len(docs)):
    for j in range(len(docs[i])):
        if docs[i][j] not in freq.keys():
            freq[docs[i][j]] = 1
        else:
            freq[docs[i][j]] += 1
            
freq = {k:v for k, v in sorted(freq.items(), key=lambda item: item[1])}

In [186]:
unk_tags,unk_words = [],[]
for i in range(len(docs)):
    for j in range(len(docs[i])):
        if freq[docs[i][j]] < 2:
            unk_words.append(docs[i][j])
            unk_tags.append(tags[i][j])

In [187]:
len(unk_words)

17592

<br>

## Unknown words trend analysis

In [188]:
nouns = ["action", "age", "ance", "cy", "ee", "ence", "er", "hood", "ion", "ism", "ist", "ity", "ling",
               "ment", "ness", "or", "ry", "scape", "ship", "dom", "ty"]
nouns_plural = ["actions", "ages", "ances", "cies", "ees", "ences", "ers", "hoods", "ions", "isms", "ists", "ities", "lings",
               "ments", "nesses", "ors", "ries", "scapes", "ships", "doms", "ties"]
verbs = ["ed", "ify", "ise", "ize", "ate", "ing"]
adjectives = ["ous", "ese", "ful", "i", "ian", "ible", "ic", "ish", "ive", "less", "ly", "able"]
adverbs = ["wise", "wards", "ward"]
high_nos = ["million", "billion"]


<br>

## Transition Matrix (Add-k smoothing with k=0.01)

In [189]:
matrix = np.zeros((num_tags,num_tags))
transition_matrix = pd.DataFrame(matrix, columns=pos, index=pos)

In [190]:
for i in range(len(x_train["word"])-1):
    a,b = y_train["tag"][i],y_train["tag"][i+1]
    transition_matrix.at[a,b]+=1

In [191]:
transition_matrix["sum"] = transition_matrix.sum(axis=1)

In [192]:
transition_matrix = (0.01+transition_matrix.loc[:,"O":"#"]).div(transition_matrix["sum"]+0.46, axis=0)

In [193]:
transition_matrix

O       NNP             ,        CD       NNS        JJ  \
O     7.207415e-06  0.552816  7.207415e-06  0.012260  0.029558  0.055504   
NNP   2.670860e-04  0.377005  1.381108e-01  0.019783  0.024455  0.008468   
,     2.818850e-07  0.128737  2.818850e-07  0.021734  0.026723  0.041719   
CD    3.798893e-07  0.012917  9.299727e-02  0.199252  0.161301  0.037419   
NNS   2.301760e-05  0.003100  1.257538e-01  0.001755  0.010711  0.017617   
JJ    2.204758e-07  0.037194  2.952192e-02  0.016823  0.234168  0.074697   
MD    1.388029e-06  0.000834  3.610264e-03  0.000001  0.000418  0.000418   
VB    5.167035e-07  0.033173  1.720674e-02  0.020410  0.050431  0.086755   
DT    1.668656e-07  0.112301  2.186107e-03  0.022143  0.073838  0.221765   
NN    1.033000e-07  0.009504  1.134235e-01  0.006446  0.077423  0.009070   
IN    1.387011e-07  0.151295  2.427409e-03  0.059572  0.058823  0.092361   
.     4.719754e-02  0.159347  3.467832e-07  0.008566  0.035927  0.035095   
VBZ   6.184116e-07  0.060358  2.393315e-02  0.020717  0.014966  0.075323   
VBG   9.079799e-07  0.039044  1.216784e-02  0.017797  0.087621  0.074274   
CC    5.781196e-07  0.159041  8.961431e-03  0.040469  0.072266  0.112098   
VBD   4.682205e-07  0.057545  2.247505e-02  0.061852  0.023927  0.052769   
VBN   6.838795e-07  0.025988  3.419466e-02  0.011421  0.035562  0.045615   
RB    4.455244e-07  0.006594  9.663469e-02  0.040231  0.003921  0.101491   
TO    6.153672e-07  0.044061  8.005927e-04  0.080675  0.023385  0.029846   
PRP   7.789703e-07  0.001013  2.087718e-02  0.000936  0.000936  0.008180   
RBR   7.952539e-06  0.000008  5.567573e-02  0.000803  0.000803  0.327653   
WDT   3.108042e-06  0.023313  6.529996e-03  0.005598  0.017408  0.010570   
VBP   1.064344e-06  0.018840  2.096864e-02  0.009154  0.032251  0.084723   
RP    5.228868e-06  0.023012  4.392772e-02  0.021966  0.046019  0.053340   
PRP$  1.648680e-06  0.046330  3.313846e-04  0.018797  0.195040  0.245490   
JJS   7.104998e-06  0.013507  2.700610e-02  0.077452  0.145660  0.112977   
POS   1.543577e-06  0.102032  5.867135e-03  0.023618  0.130742  0.212861   
``    1.912243e-06  0.076109  1.912243e-06  0.007268  0.033466  0.116649   
EX    1.549283e-05  0.000015  4.663341e-03  0.000015  0.000015  0.000015   
''    9.813024e-04  0.136522  7.854336e-04  0.005095  0.028599  0.019981   
WP    5.742308e-06  0.022975  8.044974e-03  0.001154  0.006322  0.006322   
:     2.803640e-04  0.126305  5.579521e-04  0.128248  0.032758  0.040253   
JJR   4.176307e-06  0.015874  3.884383e-02  0.001675  0.169980  0.048867   
WRB   6.383821e-06  0.104063  1.468917e-02  0.007667  0.070228  0.102786   
$     1.951044e-06  0.000002  1.951044e-06  0.991133  0.000002  0.008782   
NNPS  4.879334e-06  0.275199  1.317469e-01  0.000981  0.012203  0.007324   
WP$   7.724394e-05  0.046424  7.724394e-05  0.015526  0.316777  0.208636   
(     9.789909e-06  0.340699  9.789909e-06  0.029380  0.011758  0.047980   
)     9.704404e-06  0.052413  1.737185e-01  0.010685  0.021359  0.017478   
PDT   3.373136e-05  0.000034  3.373136e-05  0.000034  0.000034  0.000034   
RBS   3.120514e-05  0.000031  9.392748e-03  0.000031  0.006272  0.758316   
FW    4.890932e-05  0.225032  8.808569e-02  0.000049  0.039176  0.034285   
UH    1.551350e-04  0.000155  5.896680e-01  0.000155  0.000155  0.000155   
SYM   3.282994e-04  0.065988  3.282994e-04  0.033158  0.000328  0.098818   
LS    2.669514e-04  0.000267  2.138281e-01  0.000267  0.000267  0.000267   
#     1.093374e-04  0.000109  1.104308e-02  0.984146  0.000109  0.000109   

                MD        VB        DT        NN  ...           WP$         (  \
O     7.207415e-06  0.005052  0.165778  0.038207  ...  7.207415e-06  0.005052   
NNP   1.143398e-02  0.001038  0.002581  0.055686  ...  1.482987e-07  0.003352   
,     1.096561e-02  0.003834  0.133586  0.048851  ...  2.086231e-03  0.000367   
CD    1.975804e-03  0.000076  0.026479  0.203545  ...  3.836882e-05  0.001710   
NNS   2.753019e-02  0.003441  0.015885 

### Pandas dataframe computation time was extremely high (NumPy is much faster)

In [194]:
transition_matrix = transition_matrix.to_numpy()

<br>

## Building the refined training vocabulary (UNK frequency=1)

In [222]:
vocab = list(x_train["word"].unique())
vocab_size = len(vocab)

In [223]:
refined_vocab = [i for i in vocab if freq[i]>=2]
refined_vocab.append("UNK_num")
refined_vocab.append("UNK_pos")
refined_vocab.append("UNK_noun")
refined_vocab.append("UNK_noun_plural")
refined_vocab.append("UNK_verb")
refined_vocab.append("UNK_adj")
refined_vocab.append("UNK_adv")
refined_vocab.append("UNK_caps")
refined_vocab.append("UNK_caps_plural")
refined_vocab.append("UNK_weird")
refined_vocab.append("UNK")

In [224]:
len(refined_vocab)

19924

<br>

## Emmission matrix (Add-k smoothing with k=0.01)

In [226]:
matrix = np.zeros((len(refined_vocab),num_tags))
emmission_matrix = pd.DataFrame(matrix, columns=pos, index=refined_vocab)

In [227]:
for i in range(len(docs)):
    for j in range(len(docs[i])):
        word = docs[i][j]
        tag = tags[i][j]
        if word not in unk_words:
            emmission_matrix.at[word,tag] += 1
        else:
            if ((word in high_nos) or (any(char.isdigit() for char in word))) and ("-" not in word):
                emmission_matrix.at["UNK_num",tag] += 1
            elif word[-2:] == "'s":
                emmission_matrix.at["UNK_pos",tag] += 1
            elif any(word.endswith(suff) for suff in nouns):
                emmission_matrix.at["UNK_noun",tag] += 1
            elif any(word.endswith(suff) for suff in nouns_plural):
                emmission_matrix.at["UNK_noun_plural",tag] += 1
            elif any(word.endswith(suff) for suff in verbs):
                emmission_matrix.at["UNK_verb",tag] += 1
            elif any(word.endswith(suff) for suff in adjectives):
                emmission_matrix.at["UNK_adj",tag] += 1
            elif any(word.endswith(suff) for suff in adverbs):
                emmission_matrix.at["UNK_adv",tag] += 1
            elif word[0].isupper() and word[-1] != "s":
                emmission_matrix.at["UNK_caps",tag] += 1
            elif word[0].isupper():
                emmission_matrix.at["UNK_caps_plural",tag] += 1
            elif (any(char == "'" for char in word[:-2])) or (len(word)<3 and (word[-1]=="a" or word[-1]=="i")) or ((len(word)>1) and (any(char == "." for char in word))):
                emmission_matrix.at["UNK_weird",tag] += 1
            else:
                emmission_matrix.at["UNK",tag] += 1

In [228]:
for col in emmission_matrix.columns:
    emmission_matrix[col] = (emmission_matrix[col]+0.01)/(emmission_matrix[col].sum()+199.24)

In [229]:
emmission_matrix

O           NNP             ,            CD  \
-DOCSTART-       0.874401  1.478628e-07  2.803143e-07  3.770421e-07   
Pierre           0.000006  8.886557e-05  2.803143e-07  3.770421e-07   
Vinken           0.000006  2.972043e-05  2.803143e-07  3.770421e-07   
,                0.000006  1.478628e-07  9.943312e-01  3.770421e-07   
61               0.000006  1.478628e-07  2.803143e-07  7.544612e-04   
...                   ...           ...           ...           ...   
UNK_adv          0.000006  1.478628e-07  2.803143e-07  3.770421e-07   
UNK_caps         0.000006  4.483216e-02  2.803143e-07  3.397149e-04   
UNK_caps_plural  0.000006  4.066376e-03  2.803143e-07  3.770421e-07   
UNK_weird        0.000006  4.450672e-05  2.803143e-07  1.511939e-04   
UNK              0.000006  1.923696e-04  2.803143e-07  2.639671e-03   

                          NNS            JJ        MD            VB  \
-DOCSTART-       2.268693e-07  2.195137e-07  0.000001  5.114504e-07   
Pierre           2.268693e-07  2.195137e-07  0.000001  5.114504e-07   
Vinken           2.268693e-07  2.195137e-07  0.000001  5.114504e-07   
,                2.268693e-07  2.195137e-07  0.000001  5.114504e-07   
61               2.268693e-07  2.195137e-07  0.000001  5.114504e-07   
...                       ...           ...       ...           ...   
UNK_adv          2.291380e-05  4.412226e-05  0.000001  5.114504e-07   
UNK_caps         1.111887e-03  4.127077e-03  0.000136  2.097458e-03   
UNK_caps_plural  3.857005e-03  8.802500e-05  0.000001  5.114504e-07   
UNK_weird        2.268693e-07  2.636360e-04  0.000001  5.114504e-07   
UNK              2.130326e-02  3.031506e-02  0.000136  1.217303e-02   

                           DT            NN  ...      WP$         (         )  \
-DOCSTART-       1.663140e-07  1.030883e-07  ...  0.00003  0.000008  0.000008   
Pierre           1.663140e-07  1.030883e-07  ...  0.00003  0.000008  0.000008   
Vinken           1.663140e-07  1.030883e-07  ...  0.00003  0.000008  0.000008   
,                1.663140e-07  1.030883e-07  ...  0.00003  0.000008  0.000008   
61               1.663140e-07  1.030883e-07  ...  0.00003  0.000008  0.000008   
...                       ...           ...  ...      ...       ...       ...   
UNK_adv          1.663140e-07  1.041192e-05  ...  0.00003  0.000008  0.000008   
UNK_caps         1.663140e-07  2.587619e-03  ...  0.00003  0.000008  0.000008   
UNK_caps_plural  1.663140e-07  1.031914e-04  ...  0.00003  0.000008  0.000008   
UNK_weird        1.663140e-07  5.164723e-05  ...  0.00003  0.000008  0.000008   
UNK              1.663140e-07  1.338096e-02  ...  0.00003  0.000008  0.000008   

                     PDT       RBS        FW        UH       SYM        LS  \
-DOCSTART-       0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
Pierre           0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
Vinken           0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
,                0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
61               0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
...                  ...       ...       ...       ...       ...       ...   
UNK_adv          0.00002  0.000019  0.000025  0.000038  0.000044  0.000042   
UNK_caps         0.00002  0.001945  0.027304  0.026630  0.004406  0.000042   
UNK_caps_plural  0.00002  0.000019  0.002505  0.000038  0.000044  0.000042   
UNK_weird        0.00002  0.000019  0.002505  0.000038  0.000044  0.000042   
UNK              0.00002  0.000019  0.069462  0.007636  0.004406  0.000042   

                        #  
-DOCSTART-       0.000034  
Pierre           0.000034  
Vinken           0.000034  
,                0.000034  
61               0.000034  
...                   ...  
UNK_adv          0.000034  
UNK_caps         0.000034  
UNK_caps_plural  0.000034  
UNK_weird        0.000034  
UNK              0.000034  

[19924 rows x 46 columns]

In [230]:
emmission_matrix = emmission_matrix.to_numpy()

<br>

## Validation data 

In [203]:
x_dev

id               word
0            0         -DOCSTART-
1            1          Following
2            2                 is
3            3                  a
4            4             weekly
...        ...                ...
243016  243016  35-cents-a-gallon
243017  243017           gasoline
243018  243018               were
243019  243019            history
243020  243020                  .

[243021 rows x 2 columns]

<br>

### Splitting the words by document number (accuracy was low when document split was performed)

In [30]:
val_docs = {i:["dummy"] for i in range(462)}
count = -1
for idx,row in x_dev.iterrows():
    if(row["word"] == "-DOCSTART-"):
        count += 1
        val_docs[count][0] = row["word"]
    else:
        val_docs[count].append(row["word"])

In [31]:
val_docs

{0: ['-DOCSTART-',
  'Following',
  'is',
  'a',
  'weekly',
  'listing',
  'of',
  'unadited',
  'net',
  'asset',
  'values',
  'of',
  'publicly',
  'traded',
  'investment',
  'fund',
  'shares',
  ',',
  'reported',
  'by',
  'the',
  'companies',
  'as',
  'of',
  'Friday',
  "'s",
  'close',
  '.',
  'Also',
  'shown',
  'is',
  'the',
  'closing',
  'listed',
  'market',
  'price',
  'or',
  'a',
  'dealer-to-dealer',
  'asked',
  'price',
  'of',
  'each',
  'fund',
  "'s",
  'shares',
  ',',
  'with',
  'the',
  'percentage',
  'of',
  'difference',
  '.',
  'Closed',
  'End',
  'Bond',
  'Funds',
  'Flexible',
  'Portfolio',
  'Funds',
  'Specialized',
  'Equity',
  'and',
  'Convertible',
  'Funds',
  'a',
  '-',
  'Ex-dividend',
  '.',
  'b',
  '-',
  'As',
  'of',
  'Thursday',
  "'s",
  'close',
  '.',
  'c',
  '-',
  'Translated',
  'at',
  'Commercial',
  'Rand',
  'exchange',
  'rate',
  '.',
  'e',
  '-',
  'In',
  'Canadian',
  'dollars',
  '.',
  'f',
  '-',
  'As'

In [204]:
val_words_all, val_tags_all = [],[]
for i in x_dev["word"]:
    val_words_all.append(i)

In [205]:
print(len(val_words_all))

243021


<br>

<br>

## Viterbi algorithm

In [231]:
# HMM scores computation first step

import math 

def base_matrix(all_words,pos,emmission_matrix,transition_matrix):
    col_size = len(all_words)
    tag_tracking_mat, score_matrix = np.zeros((46,col_size)), np.zeros((46,col_size))
    
    for tag_idx in range(len(pos)):
        score_matrix[tag_idx,0] = math.log(transition_matrix[0,tag_idx]) + math.log(emmission_matrix[0,tag_idx])
    return score_matrix, tag_tracking_mat


In [232]:
# Computing the best scores for every progressive word (looping through each POS tag)

score_matrix, tag_tracking_mat = base_matrix(val_words_all,pos,emmission_matrix,transition_matrix)
row_size, col_size = score_matrix.shape

#current word loop
for j in range(1,col_size):
        
    word = val_words_all[j]
    if word in freq.keys() and freq[word]>=2:
        train_word_index = refined_vocab.index(word)
    else:
        if ((word in high_nos) or (any(char.isdigit() for char in word))) and ("-" not in word):
            train_word_index = refined_vocab.index("UNK_num")
        elif word[-2:] == "'s":
            train_word_index = refined_vocab.index("UNK_pos")
        elif any(word.endswith(suff) for suff in nouns):
            train_word_index = refined_vocab.index("UNK_noun")
        elif any(word.endswith(suff) for suff in nouns_plural):
            train_word_index = refined_vocab.index("UNK_noun_plural")
        elif any(word.endswith(suff) for suff in verbs):
            train_word_index = refined_vocab.index("UNK_verb")
        elif any(word.endswith(suff) for suff in adjectives):
            train_word_index = refined_vocab.index("UNK_adj")
        elif any(word.endswith(suff) for suff in adverbs):
            train_word_index = refined_vocab.index("UNK_adv")
        elif word[0].isupper() and word[-1] != "s":
            train_word_index = refined_vocab.index("UNK_caps")
        elif word[0].isupper():
            train_word_index = refined_vocab.index("UNK_caps_plural")
        elif (any(char == "'" for char in word[:-2])) or (len(word)<3 and (word[-1]=="a" or word[-1]=="i")) or ((len(word)>1) and (any(char == "." for char in word))):
            train_word_index = refined_vocab.index("UNK_weird")
        else:
            train_word_index = refined_vocab.index("UNK")
        
    #current tag loop
    for curr_tag_idx in range(len(pos)): 
        best_score_curr, best_tag_curr = float("-inf"), None
            
        #old tag loop
        for old_tag_idx in range(len(pos)):
            if word in freq.keys():
                temp_prob = score_matrix[old_tag_idx,j-1] + math.log(transition_matrix[old_tag_idx,curr_tag_idx]) + math.log(emmission_matrix[train_word_index,curr_tag_idx])
                if temp_prob > best_score_curr:
                    best_score_curr = temp_prob
                    best_tag_curr = old_tag_idx
            else:
                temp_prob = score_matrix[old_tag_idx,j-1] + math.log(transition_matrix[old_tag_idx,curr_tag_idx]) + math.log(emmission_matrix[train_word_index,curr_tag_idx])
                if temp_prob > best_score_curr:
                    best_score_curr = temp_prob
                    best_tag_curr = old_tag_idx
            
        score_matrix[curr_tag_idx,j] = best_score_curr
        tag_tracking_mat[curr_tag_idx,j] = best_tag_curr
            
                        

In [233]:
#Tracing the best path from the last tag

result = []
for rev in range(col_size-1,0,-1): 
    if rev == col_size-1:
        best_score_found = float("-inf")
        for t in range(len(pos)):
            if score_matrix[t,rev] > best_score_found:
                best_score_found = score_matrix[t,rev]
                best_tag = pos[t]
                prev_tag = pos[int(tag_tracking_mat[t,rev])]
        result.append(best_tag)
        result.append(prev_tag)
    else:
        result.append(pos[int(tag_tracking_mat[pos.index(result[-1]),rev])])

result = result[::-1]

<br>

# Testing how Viterbi performs on validation data

## 1. Total accuracy

In [210]:
val_true = list(y_dev["tag"])

In [234]:
count = 0
for i in range(len(result)):
    if result[i] == val_true[i]:
        count += 1

print(str(count) + " out of " + str(243021) + " total values matched.")
print("\nTotal accuracy on validation set: ")
print((count/len(result))*100)

231253 out of 243021 total values matched.

Total accuracy on validation set: 
95.15762012336383


<br>

## 2. Unknown words accuracy

In [235]:
total, matched = 0,0
wrongly_guessed = {}

for j in range(col_size):
    word = val_words_all[j]
    if word not in freq.keys():
        total += 1
        if result[j] == val_true[j]:
            matched += 1
        else:
            if (val_true[j],result[j]) in wrongly_guessed.keys():
                wrongly_guessed[(val_true[j],result[j])] += 1
            else:
                wrongly_guessed[(val_true[j],result[j])] = 1

print(str(matched) + " out of " + str(total) + " unknown values matched.")
print("\nUnknown words accuracy: \n" + str((matched*100)/total))

6540 out of 8851 unknown values matched.

Unknown words accuracy: 
73.88995593718224


In [236]:
wrongly_guessed = {k:v for k,v in sorted(wrongly_guessed.items(), key = lambda item: item[1], reverse = True)}
wrongly_guessed

{('NN', 'JJ'): 336,
 ('NN', 'NNP'): 169,
 ('NNP', 'JJ'): 150,
 ('NNS', 'NN'): 147,
 ('NNP', 'NN'): 114,
 ('NN', 'NNS'): 101,
 ('JJ', 'NNP'): 97,
 ('NNS', 'NNP'): 66,
 ('JJ', 'NN'): 66,
 ('VBG', 'JJ'): 47,
 ('VBN', 'VBG'): 43,
 ('JJ', 'RB'): 43,
 ('VBN', 'JJ'): 42,
 ('NNPS', 'NNP'): 39,
 ('VB', 'NNP'): 34,
 ('JJ', 'VBN'): 32,
 ('NNPS', 'NNS'): 32,
 ('NNS', 'JJ'): 32,
 ('NNP', 'NNS'): 30,
 ('VBD', 'VBG'): 27,
 ('RB', 'JJ'): 24,
 ('VBG', 'NN'): 21,
 ('RB', 'NNP'): 20,
 ('VBZ', 'NN'): 20,
 ('NN', 'VBG'): 19,
 ('VB', 'JJ'): 18,
 ('VBD', 'NNP'): 17,
 ('VBZ', 'NNS'): 16,
 ('VBG', 'VBN'): 16,
 ('JJ', 'NNS'): 16,
 ('VBG', 'VBD'): 15,
 ('NNS', 'VBZ'): 14,
 ('JJS', 'JJ'): 14,
 ('JJ', 'VBG'): 14,
 ('JJR', 'JJ'): 13,
 ('JJ', 'CD'): 12,
 ('VBN', 'NNP'): 12,
 ('VBD', 'JJ'): 12,
 ('NNP', 'RB'): 12,
 ('VBG', 'NNP'): 11,
 ('NN', 'VBZ'): 11,
 ('JJ', 'VB'): 11,
 ('$', 'NNP'): 11,
 ('VBZ', 'NNP'): 10,
 ('NNP', 'NNPS'): 10,
 ('VBD', 'VBN'): 10,
 ('CD', 'NN'): 10,
 ('NNP', 'CD'): 9,
 ('NNS', 'NNPS'): 9,
 ('V

<br>

## 3. F1 score for validation data:

In [237]:
from sklearn.metrics import f1_score
f1 = f1_score(val_true, result, average="weighted")
print(f1)

0.9521031888184739


<br>

## 4. Metrics report:

In [238]:
from sklearn.metrics import classification_report
report = classification_report(val_true, result)
print(report)

              precision    recall  f1-score   support

           #       1.00      1.00      1.00        46
           $       1.00      0.99      1.00      2051
          ''       1.00      1.00      1.00      1664
           (       1.00      1.00      1.00       309
           )       1.00      1.00      1.00       316
           ,       1.00      1.00      1.00     12558
           .       1.00      1.00      1.00     10078
           :       1.00      1.00      1.00      1187
          CC       0.99      0.99      0.99      6157
          CD       0.99      0.99      0.99      9509
          DT       1.00      0.99      0.99     21003
          EX       0.94      0.98      0.96       210
          FW       0.10      0.18      0.13        22
          IN       0.98      0.97      0.98     25237
          JJ       0.85      0.91      0.88     15277
         JJR       0.84      0.88      0.86       837
         JJS       0.96      0.90      0.93       511
          LS       0.70    

<br>

# TESTING

In [225]:
x_test

id        word
0            0  -DOCSTART-
1            1       Times
2            2         may
3            3          be
4            4       tough
...        ...         ...
236577  236577        them
236578  236578        here
236579  236579        with
236580  236580          us
236581  236581           .

[236582 rows x 2 columns]

In [386]:
len(test_pred)

236582

In [143]:
test_words_all = []
for i in x_test["word"]:
    test_words_all.append(i)

In [239]:
# Perform Viterbi for Test data here

score_matrix, tag_tracking_mat = base_matrix(test_words_all,pos,emmission_matrix,transition_matrix)
row_size, col_size = score_matrix.shape

#current word loop
for j in range(1,col_size):
        
    word = test_words_all[j]
    if word in freq.keys() and freq[word]>=2:
        train_word_index = refined_vocab.index(word)
    else:
        if ((word in high_nos) or (any(char.isdigit() for char in word))) and ("-" not in word):
            train_word_index = refined_vocab.index("UNK_num")
        elif word[-2:] == "'s":
            train_word_index = refined_vocab.index("UNK_pos")
        elif any(word.endswith(suff) for suff in nouns):
            train_word_index = refined_vocab.index("UNK_noun")
        elif any(word.endswith(suff) for suff in nouns_plural):
            train_word_index = refined_vocab.index("UNK_noun_plural")
        elif any(word.endswith(suff) for suff in verbs):
            train_word_index = refined_vocab.index("UNK_verb")
        elif any(word.endswith(suff) for suff in adjectives):
            train_word_index = refined_vocab.index("UNK_adj")
        elif any(word.endswith(suff) for suff in adverbs):
            train_word_index = refined_vocab.index("UNK_adv")
        elif word[0].isupper() and word[-1] != "s":
            train_word_index = refined_vocab.index("UNK_caps")
        elif word[0].isupper():
            train_word_index = refined_vocab.index("UNK_caps_plural")
        elif (any(char == "'" for char in word[:-2])) or (len(word)<3 and (word[-1]=="a" or word[-1]=="i")) or ((len(word)>1) and (any(char == "." for char in word))):
            train_word_index = refined_vocab.index("UNK_weird")
        else:
            train_word_index = refined_vocab.index("UNK")
        
    #current tag loop
    for curr_tag_idx in range(len(pos)): 
        best_score_curr, best_tag_curr = float("-inf"), None
            
        #old tag loop
        for old_tag_idx in range(len(pos)):
            if word in freq.keys():
                temp_prob = score_matrix[old_tag_idx,j-1] + math.log(transition_matrix[old_tag_idx,curr_tag_idx]) + math.log(emmission_matrix[train_word_index,curr_tag_idx])
                if temp_prob > best_score_curr:
                    best_score_curr = temp_prob
                    best_tag_curr = old_tag_idx
            else:
                temp_prob = score_matrix[old_tag_idx,j-1] + math.log(transition_matrix[old_tag_idx,curr_tag_idx]) + math.log(emmission_matrix[train_word_index,curr_tag_idx])
                if temp_prob > best_score_curr:
                    best_score_curr = temp_prob
                    best_tag_curr = old_tag_idx
            
        score_matrix[curr_tag_idx,j] = best_score_curr
        tag_tracking_mat[curr_tag_idx,j] = best_tag_curr
        

In [240]:
result_test = []
for rev in range(col_size-1,0,-1): 
    if rev == col_size-1:
        best_score_found = float("-inf")
        for t in range(len(pos)):
            if score_matrix[t,rev] > best_score_found:
                best_score_found = score_matrix[t,rev]
                best_tag = pos[t]
                prev_tag = pos[int(tag_tracking_mat[t,rev])]
        result_test.append(best_tag)
        result_test.append(prev_tag)
    else:
        result_test.append(pos[int(tag_tracking_mat[pos.index(result_test[-1]),rev])])

result_test = result_test[::-1]

In [241]:
result_test

['O',
 'NNP',
 'MD',
 'VB',
 'JJ',
 'IN',
 'NNP',
 'NNP',
 'IN',
 'DT',
 ',',
 'CC',
 'DT',
 'JJ',
 'NNS',
 'VBP',
 'VBG',
 'IN',
 'RB',
 'RB',
 'RB',
 ':',
 'CC',
 'JJR',
 '.',
 'IN',
 'NNP',
 'NNP',
 'NNP',
 ',',
 'IN',
 'NN',
 ',',
 'DT',
 'CD',
 'NN',
 'NNS',
 'VBN',
 'IN',
 'NNP',
 'NNP',
 '``',
 'NNP',
 "''",
 'NNP',
 'VBD',
 'DT',
 'NN',
 'NN',
 'TO',
 '$',
 'CD',
 'CD',
 'IN',
 'DT',
 'JJ',
 'NN',
 'VBD',
 'NNP',
 'CD',
 'IN',
 '$',
 'CD',
 'CD',
 'IN',
 'DT',
 'CD',
 'NNS',
 'VBD',
 'NNP',
 'CD',
 ',',
 'CD',
 '.',
 'DT',
 'NNS',
 'VBP',
 'RB',
 'VB',
 'JJ',
 'NNS',
 'IN',
 'NNS',
 'IN',
 'NNP',
 'NNP',
 'NN',
 '.',
 'NNP',
 'NNP',
 'PRP',
 'VBD',
 'VBN',
 '$',
 'CD',
 'CD',
 ',',
 'IN',
 'DT',
 'JJ',
 '$',
 'CD',
 'CD',
 'IN',
 'NNS',
 ',',
 'RB',
 'IN',
 '$',
 'CD',
 'CD',
 'DT',
 'NN',
 'IN',
 '.',
 'DT',
 'NN',
 'VBZ',
 'VBN',
 'IN',
 'DT',
 'NN',
 'NN',
 'POS',
 'JJS',
 'JJ',
 'NN',
 'VBN',
 'IN',
 'DT',
 'NNPS',
 'CC',
 'NNP',
 'NNP',
 '.',
 'IN',
 'PRP',
 'VBZ',
 'IN',


In [242]:
import csv

# field names 
fields = ['id','tag'] 
    
# data rows of csv file 
rows = [[i,result_test[i]] for i in range(236582)] 
  
with open('test_y.csv', 'w') as f:
      
    # using csv.writer method from CSV package
    write = csv.writer(f)
      
    write.writerow(fields)
    write.writerows(rows)